In [1]:
from torch import nn
import torch
import numpy as np
from scipy import sparse
import os
import sys
from lattice import KH

/home/user/miniconda3/envs/py39/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
import rms
# u = np.load("array/torch/KH/3site/smel/Jx_1_Jy_1_Jz_1_hx_0_hz_0/e_100_lr_0.0005/loss_8.195263/u/0.npy")
u = np.load("array/torch/KH/3site/smel/Jx_1_Jy_1_Jz_1_hx_0_hz_0/e_20_lr_0.1/loss_11.958496/u/0.npy")
# H = KH.system([2,2], "3site", {"Jx" : -0.3, "Jy" : 0.8, "Jz" : 0.5, "hx" : 0, "hz" : 0})
# H_list, sps = KH.local("3site", {"Jx" : 1, "Jy" : 1, "Jz" : 1, "hx" : 0, "hz" : 0})
H = KH.system([2,2], "3site", {"Jx" : -0.3, "Jy" : 0.8, "Jz" : 0.5, "hx" : 0, "hz" : 0})
H_list, sps = KH.local("3site", {"Jx" : -0.3, "Jy" : 0.8, "Jz" : 0.5, "hx" : 0, "hz" : 0})


In [4]:
# U = np.kron(u,u)
# U = np.kron(U, U)
# U = np.kron(U, U)
U = np.kron(np.kron(u,u), u)
U = np.kron(U, U)
U = np.kron(U, U)

MemoryError: Unable to allocate 512. GiB for an array with shape (262144, 262144) and data type float64

In [30]:
H_s = rms.stoquastic(H)
H_u = rms.stoquastic(U @ H @ U.T)
Es = np.linalg.eigvalsh(H)
Es_s = np.linalg.eigvalsh(H_s)
Es_u = np.linalg.eigvalsh(H_u)

In [31]:
T = 1
b = 1 / T
N = 12
z = np.exp(-Es * b)
z_s = np.exp(-Es_s * b)
z_u = np.exp(-Es_u * b)
e = (Es * z).sum() / z.sum() / N
as_s = z.sum() / z_s.sum()
as_u = z.sum() / z_u.sum()

In [32]:
Es_s, Es_u

(array([-4.82241   , -4.82240953, -3.62160948, ...,  3.51422259,
         3.95225341,  4.02227037]),
 array([-4.87225509, -4.77267739, -3.66237144, ...,  3.51273709,
         3.95217765,  4.02160057]))

In [33]:
as_s, as_u

(0.8843077389200665, 0.8841314816733753)

In [10]:
uu = np.kron(u,u)

In [11]:
UH = U @ H @ U.T

In [12]:
H_list, sps = KH.local("3site", {"Jx" : 1, "Jy" : 1, "Jz" : 1, "hx" : 0, "hz" : 0})
H_list_u = [uu @ h @ uu.T for h in H_list]
_bonds = [[0,0,2], [1,0,1], [2,0,3], [0,1,3], [1,1,0], [2,1,2], [0,2,0], [1,2,3], 
          [2,2,1], [0,3,1], [1,3,2], [2,3,0]]
bonds = [[], [], []]
for bond in _bonds:
    bonds[bond[0]].append(bond[1:])
_H_prime = rms.sum_ham(rms.stoquastic(H_list_u[0]), bonds[0], 4, 8)
_H_prime += rms.sum_ham(rms.stoquastic(H_list_u[1]), bonds[1], 4, 8)
_H_prime += rms.sum_ham(rms.stoquastic(H_list_u[2]), bonds[2], 4, 8)

_H = rms.sum_ham(rms.stoquastic(H_list[0]), bonds[0], 4, 8)
_H += rms.sum_ham(rms.stoquastic(H_list[1]), bonds[1], 4, 8)
_H += rms.sum_ham(rms.stoquastic(H_list[2]), bonds[2], 4, 8)

_HH_prime = rms.sum_ham(H_list_u[0], bonds[0], 4, 8)
_HH_prime += rms.sum_ham(H_list_u[1], bonds[1], 4, 8)
_HH_prime += rms.sum_ham(H_list_u[2], bonds[2], 4, 8)

ValueError: matmul: Input operand 1 has a mismatch in its core dimension 0, with gufunc signature (n?,k),(k,m?)->(n?,m?) (size 64 is different from 4)

In [71]:
Es_u_prime = np.linalg.eigvalsh(_H_prime)
Es_prime = np.linalg.eigvalsh(_H)

In [72]:
z_u_prime = np.exp(-Es_u_prime * b)
z.sum() / z_u_prime.sum()

0.5878969527149649

In [73]:
z_prime = np.exp(-Es_prime * b)
z.sum() / z_prime.sum()

0.6065030480402634

In [74]:
HH = U @ H @ U.T

In [75]:
nn_state = [0,6,0,6,6,6]
x = 3
x_prime = 2

In [76]:
H_list_u[0][x * 8 + nn_state[0], x_prime * 8 + nn_state[0]], H_list_u[0][x + nn_state[0] * 8, x_prime  + nn_state[0] * 8]

(0.003559552329377712, -0.0022445367537675606)

In [9]:
def ind2state(ind):
    state = []
    for i in range(4):
        state.append(ind % 8)
        ind //= 8
    return state[::-1]

def state2ind(state):
    num = 0
    for s in state:
        num *= 8
        num += s
    return num

In [17]:
ind2state(1966)

[3, 6, 5, 6]

In [18]:
state2ind([3, 6, 5, 6])

1966

In [15]:
state = [ 3, 6, 5, 4, ]
state2 = [ 3, 6, 5, 6, ]

state_num = 0
state_num2 = 0
for e,e2 in zip(state, state2):
    state_num*= 8
    state_num2*=8
    state_num += e
    state_num2 += e2
print(HH[state_num, state_num2])

NameError: name 'HH' is not defined

In [16]:
state_num2

1966

In [79]:
a = np.argwhere(np.abs(rms.stoquastic(_HH_prime) - _H_prime) > 0.01)
for ind in a:
    print(ind2state(ind[0]), ind2state(ind[1]), _HH_prime[ind[0], ind[1]], _H_prime[ind[0], ind[1]])

[0, 0, 0, 2] [0, 0, 0, 3] -0.001914727256156081 -0.016071057013905567
[0, 0, 0, 3] [0, 0, 0, 2] -0.0019147272561560653 -0.01607105701390553
[0, 0, 1, 3] [0, 5, 1, 3] -0.00014305837597791585 -0.010505977402914465
[0, 0, 1, 4] [0, 5, 1, 4] 0.0022155026746920447 -0.012837229959059403
[0, 0, 1, 5] [0, 0, 1, 7] -0.002938034158004709 -0.015445869182616954
[0, 0, 1, 7] [0, 0, 1, 5] -0.0029380341580047165 -0.015445869182616962
[0, 0, 2, 0] [0, 0, 3, 0] -0.001914727256156081 -0.016071057013905567
[0, 0, 2, 3] [0, 0, 3, 3] 0.003951789302251001 -0.017385863662351606
[0, 0, 2, 3] [0, 2, 2, 3] -0.002363924373804811 -0.01304141520446187
[0, 0, 2, 4] [0, 0, 3, 4] -0.00184968590396987 -0.016137497240024987
[0, 0, 2, 4] [0, 2, 2, 4] -0.0024069047164166544 -0.013087295815091759
[0, 0, 2, 4] [0, 5, 2, 4] 0.0018911549673485074 -0.012277500331486054
[0, 0, 2, 5] [0, 0, 2, 7] -0.0029337781209320896 -0.015448915713923221
[0, 0, 2, 5] [0, 0, 3, 5] -0.0018658913279083877 -0.01602867753923435
[0, 0, 2, 6] [0, 0

In [37]:
P = np.zeros_like(H)
for ind in range(len(P)):
    state_ = ind2state(ind)
    for i in range(4):
        state = state_.copy()
        for x in range(8):
            state[i] = x
            ind_ = state2ind(state)
            P[ind, ind_] = 1
    P[ind, ind] = 0

In [28]:
a = np.argwhere(P)
for ind in a:
    print(ind2state(ind[0]), ind2state(ind[1]))

[0, 0, 0, 0] [0, 0, 0, 0]
[0, 0, 0, 0] [0, 0, 0, 1]
[0, 0, 0, 0] [0, 0, 0, 2]
[0, 0, 0, 0] [0, 0, 0, 3]
[0, 0, 0, 0] [0, 0, 0, 4]
[0, 0, 0, 0] [0, 0, 0, 5]
[0, 0, 0, 0] [0, 0, 0, 6]
[0, 0, 0, 0] [0, 0, 0, 7]
[0, 0, 0, 0] [0, 0, 1, 0]
[0, 0, 0, 0] [0, 0, 2, 0]
[0, 0, 0, 0] [0, 0, 3, 0]
[0, 0, 0, 0] [0, 0, 4, 0]
[0, 0, 0, 0] [0, 0, 5, 0]
[0, 0, 0, 0] [0, 0, 6, 0]
[0, 0, 0, 0] [0, 0, 7, 0]
[0, 0, 0, 0] [0, 1, 0, 0]
[0, 0, 0, 0] [0, 2, 0, 0]
[0, 0, 0, 0] [0, 3, 0, 0]
[0, 0, 0, 0] [0, 4, 0, 0]
[0, 0, 0, 0] [0, 5, 0, 0]
[0, 0, 0, 0] [0, 6, 0, 0]
[0, 0, 0, 0] [0, 7, 0, 0]
[0, 0, 0, 0] [1, 0, 0, 0]
[0, 0, 0, 0] [2, 0, 0, 0]
[0, 0, 0, 0] [3, 0, 0, 0]
[0, 0, 0, 0] [4, 0, 0, 0]
[0, 0, 0, 0] [5, 0, 0, 0]
[0, 0, 0, 0] [6, 0, 0, 0]
[0, 0, 0, 0] [7, 0, 0, 0]
[0, 0, 0, 1] [0, 0, 0, 0]
[0, 0, 0, 1] [0, 0, 0, 1]
[0, 0, 0, 1] [0, 0, 0, 2]
[0, 0, 0, 1] [0, 0, 0, 3]
[0, 0, 0, 1] [0, 0, 0, 4]
[0, 0, 0, 1] [0, 0, 0, 5]
[0, 0, 0, 1] [0, 0, 0, 6]
[0, 0, 0, 1] [0, 0, 0, 7]
[0, 0, 0, 1] [0, 0, 1, 1]
[0, 0, 0, 1]

[1, 0, 0, 0] [1, 1, 0, 0]
[1, 0, 0, 0] [1, 2, 0, 0]
[1, 0, 0, 0] [1, 3, 0, 0]
[1, 0, 0, 0] [1, 4, 0, 0]
[1, 0, 0, 0] [1, 5, 0, 0]
[1, 0, 0, 0] [1, 6, 0, 0]
[1, 0, 0, 0] [1, 7, 0, 0]
[1, 0, 0, 0] [2, 0, 0, 0]
[1, 0, 0, 0] [3, 0, 0, 0]
[1, 0, 0, 0] [4, 0, 0, 0]
[1, 0, 0, 0] [5, 0, 0, 0]
[1, 0, 0, 0] [6, 0, 0, 0]
[1, 0, 0, 0] [7, 0, 0, 0]
[1, 0, 0, 1] [0, 0, 0, 1]
[1, 0, 0, 1] [1, 0, 0, 0]
[1, 0, 0, 1] [1, 0, 0, 1]
[1, 0, 0, 1] [1, 0, 0, 2]
[1, 0, 0, 1] [1, 0, 0, 3]
[1, 0, 0, 1] [1, 0, 0, 4]
[1, 0, 0, 1] [1, 0, 0, 5]
[1, 0, 0, 1] [1, 0, 0, 6]
[1, 0, 0, 1] [1, 0, 0, 7]
[1, 0, 0, 1] [1, 0, 1, 1]
[1, 0, 0, 1] [1, 0, 2, 1]
[1, 0, 0, 1] [1, 0, 3, 1]
[1, 0, 0, 1] [1, 0, 4, 1]
[1, 0, 0, 1] [1, 0, 5, 1]
[1, 0, 0, 1] [1, 0, 6, 1]
[1, 0, 0, 1] [1, 0, 7, 1]
[1, 0, 0, 1] [1, 1, 0, 1]
[1, 0, 0, 1] [1, 2, 0, 1]
[1, 0, 0, 1] [1, 3, 0, 1]
[1, 0, 0, 1] [1, 4, 0, 1]
[1, 0, 0, 1] [1, 5, 0, 1]
[1, 0, 0, 1] [1, 6, 0, 1]
[1, 0, 0, 1] [1, 7, 0, 1]
[1, 0, 0, 1] [2, 0, 0, 1]
[1, 0, 0, 1] [3, 0, 0, 1]
[1, 0, 0, 1]

[1, 6, 7, 7] [1, 6, 5, 7]
[1, 6, 7, 7] [1, 6, 6, 7]
[1, 6, 7, 7] [1, 6, 7, 0]
[1, 6, 7, 7] [1, 6, 7, 1]
[1, 6, 7, 7] [1, 6, 7, 2]
[1, 6, 7, 7] [1, 6, 7, 3]
[1, 6, 7, 7] [1, 6, 7, 4]
[1, 6, 7, 7] [1, 6, 7, 5]
[1, 6, 7, 7] [1, 6, 7, 6]
[1, 6, 7, 7] [1, 6, 7, 7]
[1, 6, 7, 7] [1, 7, 7, 7]
[1, 6, 7, 7] [2, 6, 7, 7]
[1, 6, 7, 7] [3, 6, 7, 7]
[1, 6, 7, 7] [4, 6, 7, 7]
[1, 6, 7, 7] [5, 6, 7, 7]
[1, 6, 7, 7] [6, 6, 7, 7]
[1, 6, 7, 7] [7, 6, 7, 7]
[1, 7, 0, 0] [0, 7, 0, 0]
[1, 7, 0, 0] [1, 0, 0, 0]
[1, 7, 0, 0] [1, 1, 0, 0]
[1, 7, 0, 0] [1, 2, 0, 0]
[1, 7, 0, 0] [1, 3, 0, 0]
[1, 7, 0, 0] [1, 4, 0, 0]
[1, 7, 0, 0] [1, 5, 0, 0]
[1, 7, 0, 0] [1, 6, 0, 0]
[1, 7, 0, 0] [1, 7, 0, 0]
[1, 7, 0, 0] [1, 7, 0, 1]
[1, 7, 0, 0] [1, 7, 0, 2]
[1, 7, 0, 0] [1, 7, 0, 3]
[1, 7, 0, 0] [1, 7, 0, 4]
[1, 7, 0, 0] [1, 7, 0, 5]
[1, 7, 0, 0] [1, 7, 0, 6]
[1, 7, 0, 0] [1, 7, 0, 7]
[1, 7, 0, 0] [1, 7, 1, 0]
[1, 7, 0, 0] [1, 7, 2, 0]
[1, 7, 0, 0] [1, 7, 3, 0]
[1, 7, 0, 0] [1, 7, 4, 0]
[1, 7, 0, 0] [1, 7, 5, 0]
[1, 7, 0, 0]

[2, 5, 5, 0] [2, 5, 5, 4]
[2, 5, 5, 0] [2, 5, 5, 5]
[2, 5, 5, 0] [2, 5, 5, 6]
[2, 5, 5, 0] [2, 5, 5, 7]
[2, 5, 5, 0] [2, 5, 6, 0]
[2, 5, 5, 0] [2, 5, 7, 0]
[2, 5, 5, 0] [2, 6, 5, 0]
[2, 5, 5, 0] [2, 7, 5, 0]
[2, 5, 5, 0] [3, 5, 5, 0]
[2, 5, 5, 0] [4, 5, 5, 0]
[2, 5, 5, 0] [5, 5, 5, 0]
[2, 5, 5, 0] [6, 5, 5, 0]
[2, 5, 5, 0] [7, 5, 5, 0]
[2, 5, 5, 1] [0, 5, 5, 1]
[2, 5, 5, 1] [1, 5, 5, 1]
[2, 5, 5, 1] [2, 0, 5, 1]
[2, 5, 5, 1] [2, 1, 5, 1]
[2, 5, 5, 1] [2, 2, 5, 1]
[2, 5, 5, 1] [2, 3, 5, 1]
[2, 5, 5, 1] [2, 4, 5, 1]
[2, 5, 5, 1] [2, 5, 0, 1]
[2, 5, 5, 1] [2, 5, 1, 1]
[2, 5, 5, 1] [2, 5, 2, 1]
[2, 5, 5, 1] [2, 5, 3, 1]
[2, 5, 5, 1] [2, 5, 4, 1]
[2, 5, 5, 1] [2, 5, 5, 0]
[2, 5, 5, 1] [2, 5, 5, 1]
[2, 5, 5, 1] [2, 5, 5, 2]
[2, 5, 5, 1] [2, 5, 5, 3]
[2, 5, 5, 1] [2, 5, 5, 4]
[2, 5, 5, 1] [2, 5, 5, 5]
[2, 5, 5, 1] [2, 5, 5, 6]
[2, 5, 5, 1] [2, 5, 5, 7]
[2, 5, 5, 1] [2, 5, 6, 1]
[2, 5, 5, 1] [2, 5, 7, 1]
[2, 5, 5, 1] [2, 6, 5, 1]
[2, 5, 5, 1] [2, 7, 5, 1]
[2, 5, 5, 1] [3, 5, 5, 1]
[2, 5, 5, 1]

[3, 5, 1, 2] [7, 5, 1, 2]
[3, 5, 1, 3] [0, 5, 1, 3]
[3, 5, 1, 3] [1, 5, 1, 3]
[3, 5, 1, 3] [2, 5, 1, 3]
[3, 5, 1, 3] [3, 0, 1, 3]
[3, 5, 1, 3] [3, 1, 1, 3]
[3, 5, 1, 3] [3, 2, 1, 3]
[3, 5, 1, 3] [3, 3, 1, 3]
[3, 5, 1, 3] [3, 4, 1, 3]
[3, 5, 1, 3] [3, 5, 0, 3]
[3, 5, 1, 3] [3, 5, 1, 0]
[3, 5, 1, 3] [3, 5, 1, 1]
[3, 5, 1, 3] [3, 5, 1, 2]
[3, 5, 1, 3] [3, 5, 1, 3]
[3, 5, 1, 3] [3, 5, 1, 4]
[3, 5, 1, 3] [3, 5, 1, 5]
[3, 5, 1, 3] [3, 5, 1, 6]
[3, 5, 1, 3] [3, 5, 1, 7]
[3, 5, 1, 3] [3, 5, 2, 3]
[3, 5, 1, 3] [3, 5, 3, 3]
[3, 5, 1, 3] [3, 5, 4, 3]
[3, 5, 1, 3] [3, 5, 5, 3]
[3, 5, 1, 3] [3, 5, 6, 3]
[3, 5, 1, 3] [3, 5, 7, 3]
[3, 5, 1, 3] [3, 6, 1, 3]
[3, 5, 1, 3] [3, 7, 1, 3]
[3, 5, 1, 3] [4, 5, 1, 3]
[3, 5, 1, 3] [5, 5, 1, 3]
[3, 5, 1, 3] [6, 5, 1, 3]
[3, 5, 1, 3] [7, 5, 1, 3]
[3, 5, 1, 4] [0, 5, 1, 4]
[3, 5, 1, 4] [1, 5, 1, 4]
[3, 5, 1, 4] [2, 5, 1, 4]
[3, 5, 1, 4] [3, 0, 1, 4]
[3, 5, 1, 4] [3, 1, 1, 4]
[3, 5, 1, 4] [3, 2, 1, 4]
[3, 5, 1, 4] [3, 3, 1, 4]
[3, 5, 1, 4] [3, 4, 1, 4]
[3, 5, 1, 4]

[4, 3, 6, 5] [4, 3, 6, 4]
[4, 3, 6, 5] [4, 3, 6, 5]
[4, 3, 6, 5] [4, 3, 6, 6]
[4, 3, 6, 5] [4, 3, 6, 7]
[4, 3, 6, 5] [4, 3, 7, 5]
[4, 3, 6, 5] [4, 4, 6, 5]
[4, 3, 6, 5] [4, 5, 6, 5]
[4, 3, 6, 5] [4, 6, 6, 5]
[4, 3, 6, 5] [4, 7, 6, 5]
[4, 3, 6, 5] [5, 3, 6, 5]
[4, 3, 6, 5] [6, 3, 6, 5]
[4, 3, 6, 5] [7, 3, 6, 5]
[4, 3, 6, 6] [0, 3, 6, 6]
[4, 3, 6, 6] [1, 3, 6, 6]
[4, 3, 6, 6] [2, 3, 6, 6]
[4, 3, 6, 6] [3, 3, 6, 6]
[4, 3, 6, 6] [4, 0, 6, 6]
[4, 3, 6, 6] [4, 1, 6, 6]
[4, 3, 6, 6] [4, 2, 6, 6]
[4, 3, 6, 6] [4, 3, 0, 6]
[4, 3, 6, 6] [4, 3, 1, 6]
[4, 3, 6, 6] [4, 3, 2, 6]
[4, 3, 6, 6] [4, 3, 3, 6]
[4, 3, 6, 6] [4, 3, 4, 6]
[4, 3, 6, 6] [4, 3, 5, 6]
[4, 3, 6, 6] [4, 3, 6, 0]
[4, 3, 6, 6] [4, 3, 6, 1]
[4, 3, 6, 6] [4, 3, 6, 2]
[4, 3, 6, 6] [4, 3, 6, 3]
[4, 3, 6, 6] [4, 3, 6, 4]
[4, 3, 6, 6] [4, 3, 6, 5]
[4, 3, 6, 6] [4, 3, 6, 6]
[4, 3, 6, 6] [4, 3, 6, 7]
[4, 3, 6, 6] [4, 3, 7, 6]
[4, 3, 6, 6] [4, 4, 6, 6]
[4, 3, 6, 6] [4, 5, 6, 6]
[4, 3, 6, 6] [4, 6, 6, 6]
[4, 3, 6, 6] [4, 7, 6, 6]
[4, 3, 6, 6]

[5, 2, 4, 0] [5, 2, 4, 0]
[5, 2, 4, 0] [5, 2, 4, 1]
[5, 2, 4, 0] [5, 2, 4, 2]
[5, 2, 4, 0] [5, 2, 4, 3]
[5, 2, 4, 0] [5, 2, 4, 4]
[5, 2, 4, 0] [5, 2, 4, 5]
[5, 2, 4, 0] [5, 2, 4, 6]
[5, 2, 4, 0] [5, 2, 4, 7]
[5, 2, 4, 0] [5, 2, 5, 0]
[5, 2, 4, 0] [5, 2, 6, 0]
[5, 2, 4, 0] [5, 2, 7, 0]
[5, 2, 4, 0] [5, 3, 4, 0]
[5, 2, 4, 0] [5, 4, 4, 0]
[5, 2, 4, 0] [5, 5, 4, 0]
[5, 2, 4, 0] [5, 6, 4, 0]
[5, 2, 4, 0] [5, 7, 4, 0]
[5, 2, 4, 0] [6, 2, 4, 0]
[5, 2, 4, 0] [7, 2, 4, 0]
[5, 2, 4, 1] [0, 2, 4, 1]
[5, 2, 4, 1] [1, 2, 4, 1]
[5, 2, 4, 1] [2, 2, 4, 1]
[5, 2, 4, 1] [3, 2, 4, 1]
[5, 2, 4, 1] [4, 2, 4, 1]
[5, 2, 4, 1] [5, 0, 4, 1]
[5, 2, 4, 1] [5, 1, 4, 1]
[5, 2, 4, 1] [5, 2, 0, 1]
[5, 2, 4, 1] [5, 2, 1, 1]
[5, 2, 4, 1] [5, 2, 2, 1]
[5, 2, 4, 1] [5, 2, 3, 1]
[5, 2, 4, 1] [5, 2, 4, 0]
[5, 2, 4, 1] [5, 2, 4, 1]
[5, 2, 4, 1] [5, 2, 4, 2]
[5, 2, 4, 1] [5, 2, 4, 3]
[5, 2, 4, 1] [5, 2, 4, 4]
[5, 2, 4, 1] [5, 2, 4, 5]
[5, 2, 4, 1] [5, 2, 4, 6]
[5, 2, 4, 1] [5, 2, 4, 7]
[5, 2, 4, 1] [5, 2, 5, 1]
[5, 2, 4, 1]

[6, 1, 5, 1] [1, 1, 5, 1]
[6, 1, 5, 1] [2, 1, 5, 1]
[6, 1, 5, 1] [3, 1, 5, 1]
[6, 1, 5, 1] [4, 1, 5, 1]
[6, 1, 5, 1] [5, 1, 5, 1]
[6, 1, 5, 1] [6, 0, 5, 1]
[6, 1, 5, 1] [6, 1, 0, 1]
[6, 1, 5, 1] [6, 1, 1, 1]
[6, 1, 5, 1] [6, 1, 2, 1]
[6, 1, 5, 1] [6, 1, 3, 1]
[6, 1, 5, 1] [6, 1, 4, 1]
[6, 1, 5, 1] [6, 1, 5, 0]
[6, 1, 5, 1] [6, 1, 5, 1]
[6, 1, 5, 1] [6, 1, 5, 2]
[6, 1, 5, 1] [6, 1, 5, 3]
[6, 1, 5, 1] [6, 1, 5, 4]
[6, 1, 5, 1] [6, 1, 5, 5]
[6, 1, 5, 1] [6, 1, 5, 6]
[6, 1, 5, 1] [6, 1, 5, 7]
[6, 1, 5, 1] [6, 1, 6, 1]
[6, 1, 5, 1] [6, 1, 7, 1]
[6, 1, 5, 1] [6, 2, 5, 1]
[6, 1, 5, 1] [6, 3, 5, 1]
[6, 1, 5, 1] [6, 4, 5, 1]
[6, 1, 5, 1] [6, 5, 5, 1]
[6, 1, 5, 1] [6, 6, 5, 1]
[6, 1, 5, 1] [6, 7, 5, 1]
[6, 1, 5, 1] [7, 1, 5, 1]
[6, 1, 5, 2] [0, 1, 5, 2]
[6, 1, 5, 2] [1, 1, 5, 2]
[6, 1, 5, 2] [2, 1, 5, 2]
[6, 1, 5, 2] [3, 1, 5, 2]
[6, 1, 5, 2] [4, 1, 5, 2]
[6, 1, 5, 2] [5, 1, 5, 2]
[6, 1, 5, 2] [6, 0, 5, 2]
[6, 1, 5, 2] [6, 1, 0, 2]
[6, 1, 5, 2] [6, 1, 1, 2]
[6, 1, 5, 2] [6, 1, 2, 2]
[6, 1, 5, 2]

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

